<a href="https://colab.research.google.com/github/olya-ds/practical-work/blob/main/STT_Google_API_and_Vosk_%2B_metrics.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Модуль для распознавания текста из речи

## 1. Google API

In [1]:
!pip install SpeechRecognition
!pip install datasets
!pip install jiwer
!pip install pydub

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 32.8 MB 1.2 MB/s 
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 362 kB 12.8 MB/s 
     |████████████████████████████████| 140 kB 78.8 MB/s 
     |████████████████████████████████| 1.1 MB 67.2 MB/s 
     |████████████████████████████████| 212 kB 64.5 MB/s 
     |████████████████████████████████| 86 kB 6.9 MB/s 
     |████████████████████████████████| 596 kB 72.5 MB/s 
     |████████████████████████████████| 127 kB 89.9 MB/s 
     |████████████████████████████████| 271 kB 73.9 MB/s 
     |████████████████████████████████| 144 kB 74.9 MB/s 
     |████████████████████████████████| 94 kB 3.2 MB/s 
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3
  Attempt

In [1]:
# импортирую бибилиотеки

import pandas as pd
import speech_recognition as sr
from datasets import load_metric
from jiwer import compute_measures
import re
from pydub import AudioSegment
import IPython

In [2]:
# подключаю google drive

from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [3]:
path = '/content/drive/MyDrive/Practical work/data for practical work/'

### Распознавание текста

In [4]:
# функция для конвертирования файла и распознавания текста

def recognize_record(open_file, save_file):
    sound = AudioSegment.from_file(open_file, "mp4")
    sound = sound.export (save_file, format ="wav")

    r = sr.Recognizer()

    with sr.AudioFile(sound) as source:

        # слушаю данные (загрузка аудио в память) с 100 секунды 100 секунд
        audio_data = r.record(source, offset=100, duration=100)
  
    # распознавание Google api (преобразование речи в текст)
    text = r.recognize_google(audio_data, language='ru')

    # обрабатываю полученный текст
    hypothesis = ' '.join(re.findall('[а-я|a-z]+', text.lower()))
    return hypothesis

In [5]:
# вывожу аудио

IPython.display.Audio(path+'/Как работает мозг Илона Маска.mp3')

In [6]:
# функция для открытия и чтения оригинального текста речи

def read_orig(filepath):
    orig = open(filepath, 'r', encoding='utf8')
    ref = orig.read()
    ref = re.sub("\n", ' ', ref)

    # обрабатываю полученный текст
    truth = ' '.join(re.findall('[а-я|a-z]+', ref.lower()))
    return truth

### Оценка качества
* **WER** (word error rate), измеряет показывает, насколько распознанный текст отличается от оригинала.
* **MER** (match error rate) это доля совпадений слов ввода-вывода, которые являются ошибками.
* **WIL** (word information lost) это простое приближение к доле потерянной словесной информации.
* **Hits** это совпадения слов между оригинальным и распознанным текстом.
* **Substitutions** это слова, которые были заменены в распознанном тексте.
* **Deletions** это слова, которые были удалены в распознаном тексте.
* **Insertions** это слова, которые были добавлены в распознаном тексте.

In [7]:
# функция для подсчета метрик и записи их в dataframe

def show_metrics(filepath, truth, hypothesis):
    metrics = compute_measures(truth, hypothesis)
    df = pd.DataFrame(columns=['Audio File Path', 'Truth', 'Hypothesis', 'WER', 'MER', 'WIL', 'WIP', 'Hits', 'Substitutions', 'Deletions', 'Insertions'])
    df.loc[len(df)] = [filepath, truth, hypothesis, round(metrics['wer'],4), round(metrics['mer'],4), round(metrics['wil'],4), round(metrics['wip'],4), metrics['hits'], metrics['substitutions'], metrics['deletions'], metrics['insertions']]
    return df

In [8]:
show_metrics(path+'/Как работает мозг Илона Маска.wav', read_orig(path+'/Как работает мозг Илона Маска.txt'), recognize_record(path+'/Как работает мозг Илона Маска.mp4', path+'/Как работает мозг Илона Маска.wav'))

Audio File Path  \
0  /content/drive/MyDrive/Practical work/data for...   

                                               Truth  \
0  год назад илон маск признался что у него синдр...   

                                          Hypothesis     WER     MER     WIL  \
0  год назад илон маск признался что у него синдр...  0.1396  0.1378  0.2329   

      WIP Hits Substitutions Deletions Insertions  
0  0.7671  194            24         4          3

## Vosk

In [ ]:
pip install vosk

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 7.2 MB 4.4 MB/s 
  Created wheel for srt: filename=srt-3.5.2-py3-none-any.whl size=22487 sha256=c16032303f7533a4908c1e8363df78b3024f98ee5d81aba18bd8358e09e99c18
  Stored in directory: /root/.cache/pip/wheels/54/c4/ec/4604122e072aebb16803c8297b7cd3f4c72073a3ee58738015
Successfully built srt


In [ ]:
# импортирую библиотеки

from py import process
from vosk import Model, KaldiRecognizer, SetLogLevel
import sys
import os
import subprocess
import torch

In [ ]:
# модель для распознавания пунктуации

punct_model, _, _, _, apply_text = torch.hub.load(repo_or_dir='snakers4/silero-models', model='silero_te')

Downloading: "https://github.com/snakers4/silero-models/archive/master.zip" to /root/.cache/torch/hub/master.zip


  0%|          | 0.00/87.5M [00:00<?, ?B/s]

In [ ]:
path = '/content/drive/MyDrive/Practical work/data for practical work/'

In [ ]:
# функция для предобработки текста

def processing(raw_text):
    r = re.compile("[а-яА-Я]+")

    raw_text = ' '.join(raw_text)
    raw_text = raw_text.replace('"', '')
    words = raw_text.split(' ')

    words = [w for w in filter(r.match, words)]

    # пунктуация
    text = ' '.join(words)
    text = text.replace('\n}', '')

    return apply_text(text, lan='ru')

In [ ]:
# функция для распознавания текста с помощью модели

def get_raw(path, model_path='/content/drive/MyDrive/Practical work/model/model'):

    SetLogLevel(0)


    sample_rate=16000
    model = Model(model_path)
    rec = KaldiRecognizer(model, sample_rate)

    process = subprocess.Popen(['ffmpeg', '-loglevel', 'quiet', '-i',
                                f"{path}",
                                '-ar', str(sample_rate) , '-ac', '1', '-f', 's16le', '-'],
                                stdout=subprocess.PIPE)

    result = []
    while True:
        data = process.stdout.read(4000)
        if len(data) == 0:
            break
        if rec.AcceptWaveform(data):
            result.append(rec.Result())

    result.append(rec.FinalResult())

    return result

In [ ]:
# применяю функцию

raw = get_raw(path+'/Как работает мозг Илона Маска.wav')
raw

['{\n  "text" : "несколько дней назад глава компании ты осла из по и сыкс илона маска дал интервью куратору тэд крису андерса но и в этом видео мы разберём некоторые любопытный момент этого разговора а также многое другое касающаяся мышления одного из самых богатых и влиятельных людей мира полная версия перевода этого интервью видео аудио и"\n}',
 '{\n  "text" : "текста уже у нас в телеграмме ссылка внизу а мы начиная"\n}',
 '{\n  "text" : ""\n}',
 '{\n  "text" : "мой канал очень часто затрагивает тему психологического здоровья я считаю это одно из важнейших вещей в жизни и я не стану рекомендовать вам обращаться к психологом и психотерапевтом если вы чувствуете что ваша эмоциональное состояние на дне или вы просто хотите лучше понять себя и свои эмоции лично мне специалист"\n}',
 '{\n  "text" : "ты не раз помогали ей сейчас я рад сообщить что партнёром этого видео стало сервис онлайн психотерапии зигмунд онлайн я пользовался услугами ребята могу гарантировать что сервис отличный все с

In [ ]:
# обрабатываю полученный текст

processing(raw)

'Несколько дней назад глава компании Ты осла из По и сыкс Илона Маска дал интервью куратору Тэд Крису Андерса, но и в этом видео мы разберём некоторые любопытный момент этого разговора, а также многое другое, касающаяся мышления одного из самых богатых и влиятельных людей мира. Полная версия перевода этого интервью, видео, аудио и текста уже у нас в телеграмме ссылка внизу. А мы начиная мой канал очень часто затрагивает тему психологического здоровья. Я считаю это одно из важнейших вещей в жизни, и я не стану рекомендовать вам обращаться к психологом и психотерапевтом. Если вы чувствуете, что ваша эмоциональное состояние на дне или вы просто хотите лучше понять себя и свои эмоции лично. Мне специалист ты не раз помогали ей сейчас я рад сообщить, что партнёром этого видео стало сервис онлайн-психотерапии. Зигмунд онлайн. Я пользовался услугами ребята могу гарантировать, что сервис отличный все специалисты. Зигмунд Зигмунд — онлайн — профессиональные психологи, психотерапевты с необходим